## Introduction / Business problem

The problem involves the recommendation of new place to the customer who wants to open a new restaurant. 
Why is this necesssary? The location of the restaurant plays a significant role in the profits of the company. Thus including analysis of the location can help to possibly increase the income of the restaurant owner(customer). 

Let's assume that the customer wants to open the restaurant somewhere in Toronta and asks us to suggest the location for restaurant. 

There are number of things to consider before opening a restaurant. Some of them are
        1. Target Customer
        2. Visibility of the shop
        3. Locality
        4. Operation time

Assume the target customer to be from Entertainment centers such as theaters, malls, amusement park etc..,We will try to find
    1. What are the High entertainment zones?
    2. What are the already existing Restaurant's Location?

## Data Collection

The data needed as of now is the location of the entertainment places and location of the restaurants (any type)

In [1]:
import pandas as pd
import numpy as np
import requests
from pandas.io.json import json_normalize
!pip install folium
import folium
!pip install geopy
from geopy.geocoders import Nominatim
import warnings
warnings.filterwarnings('ignore')
from math import sin, cos, sqrt, atan2, radians

     |████████████████████████████████| 102kB 7.5MB/s ta 0:00:011


In [2]:
lstep = 0.00899 #equivalent for 1 km lat
lonstep  = 0.012435 # equivalent for 1 km lon

The main problem in the foursquareapi is that only 50 results can be retrived at a time. So in order to get the all the restautrants, multiple number of querries has to be done.
If we were to perform all of the torronto it will take large number of calls. Thus to reduce that we will consider only 5 km around toronto city center.

In [3]:
address = 'Toronto,Canada'
geolocator = Nominatim(user_agent = 'fouresquare_agent')
location = geolocator.geocode(address)
lat = location.latitude
lon = location.longitude

In [4]:
# The code was removed by Watson Studio for sharing.

In [5]:
# The code was removed by Watson Studio for sharing.

In [6]:
def get_ent(lat, lon):
    category_id ='4d4b7104d754a06370d81259'
    url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&limit=50&radius=400'.format(client_id, client_secret, version,lat, lon, category_id)
    result = requests.get(url).json()
    res = result['response']['venues']
    en_df = json_normalize(res)
    return en_df
def clean_cat(row):
    category_list =  row['categories']
    if len(category_list) == 0:
        return None
    else:
        return category_list[0]['name']
#get_ent(lat, lon)

In [7]:
m = folium.Map([lat, lon], zoom_start = 13)
folium.Circle([lat, lon], radius = 1000, fill = False).add_to(m)
folium.Circle([lat, lon], radius = 2000, fill = False).add_to(m)
folium.Circle([lat, lon], radius = 3000, fill = False).add_to(m)
folium.Circle([lat, lon], radius = 4000, fill = False).add_to(m)
latitude = np.linspace(lat-3*lstep, lat+3*lstep, 12)
longitude = np.linspace(lon-3*lonstep, lon+3*lonstep, 12)
for ll in latitude:
        for ln in longitude:
            #folium.Marker([ll, ln], popup = '{} , {}'.format(str(ll),str(ln)), color = '#000000').add_to(m)
            folium.Marker([ll + lstep * 250 / 1000, ln + lonstep * 250 /1000]).add_to(m)
m

In [8]:
# The code was removed by Watson Studio for sharing.

In [9]:
load = True
save = False
if load:
    body = client_a99ba11c4add48de845d35d32564727e.get_object(Bucket='courseracapstone-donotdelete-pr-ybh4f3iuvmsz8d',Key='Entertain.csv')['Body']
    # add missing __iter__ method, so pandas accepts body as file-like object
    if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )
    filt_en = pd.read_csv(body)
    print('Load from the pickle file')
    print('Shape : ', filt_en.shape)
else:
    print('Creating the dataframe using foursquare api')
    en_df = pd.DataFrame()
    for ll in latitude:
        for ln in longitude:
            if en_df.empty:
                en_df = get_ent(ll + lstep * 250 / 1000, ln + lonstep * 250 /1000)
            else:
                en_df = pd.concat([en_df, get_ent(ll + lstep * 250 / 1000, ln + lonstep * 250 /1000)], axis = 0)
    print(en_df.shape)
    en_df['categories'] = en_df.apply(clean_cat, axis = 1)
    print(en_df.head())
    en_df.columns = [column.split('.')[-1] for column in en_df.columns]
    en_df.reset_index(drop=True, inplace = True)
    print(en_df.head())
    filt_en = en_df[['name', 'categories', 'lat', 'lng', 'id']]
    filt_en.columns = ['name', 'categories', 'lat', 'lng', 'id', 'venue_id']
    filt_en.drop_duplicates(inplace = True)
    if save:
        project.save_data(file_name = "Entertain.csv",data = filt_en.to_csv(index=False))
        print('Saved')
filt_en

Load from the pickle file
Shape :  (1588, 6)


name  \
0                  Ontario Place Cinesphere IMAX   
1                                  Ontario Place   
2                                Waterfall Stage   
3                The Ghost of Exhibition Stadium   
4     Echo Beach at Molson Canadian Amphitheatre   
5                           Wilderness Adventure   
6                                Budweiser Stage   
7                                   Tilt-A-Whirl   
8                                     CNE Casino   
9                     Cirque Du Soleil - Alegria   
10                           Niagara Falls @ CNE   
11                                    Echo Beach   
12                        Argos Club Section 123   
13                                     BMO Field   
14                         Wizard World Fun Park   
15                                   Section 122   
16                           Atlantis Night Club   
17                               Fire Ball @ CNE   
18                                   Section 109   
19                                   Section 115   
20                        Red Bull Records Booth   
21                                     Soak City   
22                            Wave Swinger @ CNE   
23                                  Bumper Boats   
24                                Bob's Boatyard   
25                                  Atom Blaster   
26                             OP Driving School   
27                                      Wham Bam   
28                                    4D Ontario   
29                                     in/future   
...                                          ...   
1558                           The Local Company   
1559                         The Olde Eton House   
1560                            Electric Perfume   
1561                          Down Stage Theatre   
1562                               The Downstage   
1563                                          KJ   
1564                        Vance's Party Palace   
1565        St. Michael's College School Theatre   
1566                                Neiman Music   
1567                              Own Your Voice   
1568                         Evento Chile-Canada   
1569                          Brazil Dance World   
1570                                     Pow Wow   
1571                         Write for Hollywood   
1572                   Marcia Rafelman Fine Arts   
1573                                        fddf   
1574                                Muse Gallery   
1575                            Cineplex Cinemas   
1576                    Learning by Heart Studio   
1577                                Muse Gallery   
1578                             Cineplex Office   
1579                     Woodlawn Pottery Studio   
1580                              Integral House   
1581                       Evergreen Brick Works   
1582                   The Papermill Art Gallery   
1583                                  Flashpoint   
1584                Psychic place & new age shop   
1585                              Beaches Cinema   
1586                       Navkar Family Pelaton   
1587                       Xmas Eve Fam Jamboree   

                        categories        lat        lng  \
0                    Movie Theater  43.627817 -79.418023   
1                       Theme Park  43.630577 -79.415359   
2                      Music Venue  43.628496 -79.420327   
3                          Stadium  43.631758 -79.416776   
4                      Music Venue  43.629332 -79.415072   
5                       Theme Park  43.628525 -79.421142   
6                      Music Venue  43.629374 -79.413564   
7                       Theme Park  43.629404 -79.412718   
8                           Casino  43.631960 -79.419887   
9                           Circus  43.627986 -79.413319   
10    Theme Park Ride / Attraction  43.632377 -79.417188   
11                     Music Venue  43.629409 -79.413589   
12                Football Stadium  43.

In [10]:
def get_food(lat, lon):
    query = 'restaurant' #restaurant_id
    url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&v={}&ll={},{}&query={}&radius=500&limit=50'.format(client_id, client_secret, version,lat, lon, query)
    result = requests.get(url).json()
    res = result['response']['venues']
    food_df = json_normalize(res)
    return food_df
#get_food(lat, lon)

In [11]:
load = True
save = False
if load:
    body = client_a99ba11c4add48de845d35d32564727e.get_object(Bucket='courseracapstone-donotdelete-pr-ybh4f3iuvmsz8d',Key='Food.csv')['Body']
    # add missing __iter__ method, so pandas accepts body as file-like object
    if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )
    filt_food = pd.read_csv(body)
    print('Load from the csv file')
    print('Shape : ', filt_food.shape)
else:
    food_df = pd.DataFrame()
    for ll in latitude:
        for ln in longitude:
            if food_df.empty:
                food_df = get_food(ll + lstep * 250 / 1000, ln + lonstep * 250 /1000)
            else:
                food_df = pd.concat([food_df, get_food(ll + lstep * 250 / 1000, ln + lonstep * 250 /1000)], axis = 0)
    print(food_df.shape)
    food_df['categories'] = food_df.apply(clean_cat, axis = 1)
    food_df.columns = [column.split('.')[-1] for column in food_df.columns]
    filt_food = food_df[['name', 'categories', 'lat', 'lng', 'id']]
    filt_food.columns = ['name', 'categories', 'lat', 'lng', 'id', 'venue_id']
    filt_food.reset_index(drop= True, inplace = True)
    filt_food.drop_duplicates(inplace = True)
    print(filt_food.head())
    if save:
        filt_en.to_pickle('Food.pkl')
filt_food

Load from the csv file
Shape :  (389, 6)


name  \
0                               Bar & Restaurant @ NYC   
1                              Manila Grill Restaurant   
2                                     Pearl Restaurant   
3                               Rozu Restaurant Lounge   
4                             Lusso Restaurant and Bar   
5                      Gonoe Sushi Japanese Restaurant   
6                                  Amsterdam Brewhouse   
7                                   Pearl Harbourfront   
8                             Restaurant at Number One   
9                                    SCHOOL Restaurant   
10                         INJapan Japanese Restaurant   
11                                      UFO Restaurant   
12                                   Elixir Restaurant   
13                                    Beast Restaurant   
14                        Excellent Chinese Restaurant   
15                                   Marben Restaurant   
16                               Sightlines Restaurant   
17              Ten Restaurant & Wine Bar, Port credit   
18                                  Siempre Restaurant   
19                                  Windows Restaurant   
20                                               Mi-Ne   
21   Marigold Indian Bistro | Indian Restaurants in...   
22                                      360 Restaurant   
23                                   Evviva Restaurant   
24                                      Edo Restaurant   
25                                              Subway   
26   ResoSolutions - Online Restaurant Booking Syst...   
27                   Docks Restaurant & Night Club The   
28                                    Union Restaurant   
29                                  Restaurants Canada   
..                                                 ...   
359                                    Sash Restaurant   
360                          Silk Road Restaurant 絲綢之路   
361                           Great Kitchen Restaurant   
362                                            Terroni   
363                     Beiteddine Lebanese Restaurant   
364                          Katsu Japanese Restaurant   
365                          Friendly Greek Restaurant   
366                      Simone's Caribbean Restaurant   
367                                   Camel Restaurant   
368                              The Palace Restaurant   
369                                            Asteria   
370                                             Subway   
371                      Sunshine Caribbean Restaurant   
372                            Athens Restaurant & Bar   
373                         Danforth Dragon Restaurant   
374                                  Taha's restaurant   
375                                Motorama Restaurant   
376                                  Patris Restaurant   
377                                      Sakawa Coffee   
378                                   Bloom Restaurant   
379                                Coco Pan Restaurant   
380                        Figs Restaurant Bar & Grill   
381                                  Divino Restaurant   
382                                      Chef of India   
383                                        Dairy Queen   
384                      Number One Chinese Restaurant   
385                            Greek Garden Restaurant   
386                                  Makkah Restaurant   
387                 The Corner Place Restaurant Lounge   
388                             KABSA MANDI RESTAURANT   

                      categories        lat        lng  \
0                            Bar  43.633246 -79.400224   
1                     Restaurant  43.636230 -79.411454   
2               Asian Restaurant  43.636630 -79.408052   
3    Eastern European Restaurant  43.636899 -79.406064   
4                         Lounge  43.638094 -79.380666   
5               Sushi Restaurant  43.639014 -79.385914   
6                        Brewery  43.638122 -79

In [12]:
m = folium.Map(location = [lat, lon], zoom_start = 13)
folium.Circle([lat, lon], radius=1000, color='blue', fill=False).add_to(m)
folium.Circle([lat, lon], radius=2000, color='blue', fill=False).add_to(m)
folium.Circle([lat, lon], radius=3000, color='blue', fill=False).add_to(m)
folium.Circle([lat, lon], radius=4000, color='blue', fill=False).add_to(m)
folium.Circle([lat, lon], radius=5000, color='blue', fill=False).add_to(m)
for ll in latitude:
        for ln in longitude:
            folium.Marker([ll + lstep * 250 / 1000, ln + lonstep * 250 /1000], opacity = 0.4, popup ='{}, {}'.format(ll + lstep * 250 / 1000, ln + lonstep * 250 /1000)).add_to(m)
color = ['#0000bb', '#ff0000']
for ll, ln, cat in zip(filt_en['lat'], filt_en['lng'],filt_en['categories']):
   folium.CircleMarker([ll, ln], color = color[0], fill_color = color[0], radius =2, fill = True, popup = cat, fill_opacity = 0.7).add_to(m)
for ll, ln, cat in zip(filt_food['lat'], filt_food['lng'],filt_food['categories']):
    folium.CircleMarker([ll, ln], color = color[1], fill_color = color[1], radius =2, fill = True, popup = cat, fill_opacity = 0.7).add_to(m)
m

In [13]:
from folium import plugins
from folium.plugins import HeatMap

In [14]:
en_lt =[[row['lat'], row['lng']] for i, row in filt_en.iterrows()]
m = folium.Map(location = [lat, lon], zoom_start = 12)
HeatMap(en_lt).add_to(m)
color = ['#0000bb', '#ff0000']
for ll, ln, cat in zip(filt_food['lat'], filt_food['lng'],filt_food['categories']):
    folium.CircleMarker([ll, ln], color = color[0], fill_color = color[0], radius =3, fill = True, popup = cat, fill_opacity = 0.7).add_to(m)
m

## Methodology

The main objective of this project is to identify and recommend areas with high entertain zone and low restartaurants around the vicinity.

For that, We first collected the data required (all kinds of restaurants location such as Indian restaurant, Mexican restaurant etc., and the entertainment center location).

The next step involves cleaning the collected data and stored it a csv file for later use.

We identity high density entertainment zones with Density based Clustering algorithm and calculate the number of restaurants around each cluster centers and suggest locations based on that.

## Analysis

### Density based Clustering

In [15]:
from sklearn.cluster import DBSCAN
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler

In [16]:
data = StandardScaler().fit_transform(filt_en[['lat', 'lng']])
cluster = DBSCAN(eps = 0.08, min_samples = 7)
cluster.fit(data)
np.unique(cluster.labels_)

array([-1,  0,  1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15,
       16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32,
       33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49,
       50, 51, 52])

In [17]:
print(np.random.randint(1, 255, size = (10, 3)))
colors = ["#{:02x}{:02x}{:02x}".format(x[0],x[1], x[2]) for x in np.random.randint(0, 255, size = (len(set(cluster.labels_)), 3))]
colors

[[ 81 169  80]
 [102  25 172]
 [231  72 228]
 [ 86 182 145]
 [ 81  87 247]
 [ 44   9 220]
 [ 75 235 213]
 [245 250 208]
 [ 76  94 124]
 [158  46 246]]


['#4892ae',
 '#02ab2d',
 '#1279c2',
 '#2fab2c',
 '#de8c9e',
 '#f6407e',
 '#6bfa10',
 '#a0c9a9',
 '#a9dbe5',
 '#69e481',
 '#e9c41d',
 '#214ad9',
 '#065265',
 '#0567b8',
 '#c95f2f',
 '#0e9bbb',
 '#51908b',
 '#5a27a1',
 '#b130ed',
 '#4ed8a1',
 '#0d0def',
 '#db55e7',
 '#192148',
 '#cc7caa',
 '#388045',
 '#a6766d',
 '#3d5612',
 '#c1f660',
 '#90c050',
 '#0e28ab',
 '#34c978',
 '#45e353',
 '#3fbeaf',
 '#ea03d3',
 '#49852d',
 '#e98f2a',
 '#5bc8a2',
 '#948955',
 '#e75de9',
 '#9d4c8e',
 '#a17242',
 '#a21429',
 '#590ac6',
 '#981b09',
 '#58d061',
 '#1fe510',
 '#87fa51',
 '#f217d7',
 '#deaffb',
 '#7ffcca',
 '#9c2f21',
 '#dbc067',
 '#f707af',
 '#e8d5ee']

In [18]:
minenter = 10
m = folium.Map([lat, lon], zoom_start= 13)
#colors = ['red', 'blue', 'green', 'purple', 'orange', 'darkred', 'lightred', 'beige', 'darkblue', 'darkgreen', 'cadetblue', 'darkpurple', 'white', 'pink', 'lightblue', 'lightgreen', 'gray', 'black', 'lightgray']
for ll, ln, label in zip(filt_en['lat'], filt_en['lng'], cluster.labels_):
    if label == -1:
        color = 'black'
    else:
        color = colors[label]
    folium.CircleMarker([ll, ln], radius = 2, color = color, popup = '{}'.format(label)).add_to(m)
filt_en['cluster'] = cluster.labels_
a = filt_en[filt_en['cluster'] != -1]
count = a['cluster'].value_counts()
clustid = count[count > 10].index.to_list()
print('Cluster Entertainment with more than',minenter, 'is', *clustid)
for i in clustid:
    latlon = filt_en[filt_en['cluster'] == i].loc[:, ['lat', 'lng']].apply(np.mean, axis = 0)
    folium.Marker([latlon['lat'], latlon['lng']], opacity = 0.7).add_to(m)
m

Cluster Entertainment with more than 10 is 31 41 7 12 19 17 43 27 15 47 1 32 33 18 8 3 24 26 6 45 35 11 44 34 20 28 42 48 2 10 16 52 37


The map is quite contricted. Lets plot only the points within the cluster and also the heat map of food.

In [19]:
food_lt =[[row['lat'], row['lng']] for i, row in filt_food.iterrows()]
m = folium.Map([lat, lon], zoom_start= 14)
HeatMap(food_lt).add_to(m)
for ll, ln, label, cat in zip(filt_en['lat'], filt_en['lng'], filt_en['cluster'], filt_en['categories']):
    if label == -1 or not label in clustid:
        continue
    folium.CircleMarker([ll, ln], radius = 2, color = colors[label], popup = '{}'.format(cat)).add_to(m)
clustercount = pd.DataFrame(columns = ['clusternumber', 'entertainment count', 'clustlat', 'clustlng'])
for i in clustid:
    latlon = filt_en[filt_en['cluster'] == i].loc[:, ['lat', 'lng']].apply(np.mean, axis = 0)
    clustercount = clustercount.append({'clusternumber': i, 'entertainment count': filt_en[filt_en['cluster'] == i].shape[0],
                        'clustlat': latlon['lat'], 'clustlng':latlon['lng']}, ignore_index = True)
    folium.Marker([latlon['lat'], latlon['lng']], popup = i, opacity = 0.7).add_to(m)
    folium.Circle([latlon['lat'], latlon['lng']], popup = i, opacity = 0.7, radius = 600).add_to(m)
m

Now that we have high entertain zones lets try to find the number of restaurants around 500 m of high enertainment zones.

In [20]:
def calc_distance(lat1, lon1, lat2, lon2):
    # approximate radius of earth in km
    R = 6373.0
    lat1 = radians(lat1)
    lon1 = radians(lon1)
    lat2 = radians(lat2)
    lon2 = radians(lon2)

    dlon = lon2 - lon1
    dlat = lat2 - lat1

    a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlon / 2)**2
    c = 2 * atan2(sqrt(a), sqrt(1 - a))

    distance = R * c

    return distance * 1000

In [21]:
for i, c in clustercount.iterrows():
    xc, yc = c['clustlat'], c['clustlng']
    count = 0
    for j, row in filt_food.iterrows():
        x, y = row['lat'], row['lng']
        distance = calc_distance(xc, yc, x, y)
        if distance < 300:
            count = count +1
    clustercount.loc[i, 'Count'] = count
clustercount['clusternumber'] = clustercount['clusternumber'].astype('int')
clustercount['entertainment count'] = clustercount['entertainment count'].astype('int')
clustercount['Count'] = clustercount['Count'].astype('int')
clustercount.sort_values(['Count','entertainment count'], ascending = [True, False], inplace = True)

In [26]:
clustercount

(33, 5)

Let's mark the area with no more more than 3 restaurants around 300 meters and entertainment centers greater than 10.

In [27]:
m = folium.Map([lat, lon], zoom_start = 14)
result = clustercount[(clustercount['Count'] < 4) & (clustercount['entertainment count'] > 10)]
for _, row in result.iterrows():
    address = geolocator.reverse("{},{}".format(row['clustlat'],row['clustlng'])).address
    folium.Marker([row['clustlat'],row['clustlng']], popup = address).add_to(m)
    folium.Circle([row['clustlat'],row['clustlng']], radius = 300, color='#0000ff00', fill=True, fill_color='#0066ff').add_to(m)
m

## Results and Discussion:

Our analysis shows that there around ~1550 entertainment zones around the city hall(6x6 km). The data showed that with the exception of few areas the entertainment zones are everywhere with some areas having high density of entertainment centers. The restaurants data as collected from the foursquare api indicates around 389 different kinds of restaurant. We tried to find the pockets of entertainment zones by clustering algorithm and found 52 such spots. Ensuring a minimum number of 10 entertainment centers futher reduction was performed on the selected spots. 

The number of the restaurant around 400m of the each spots was calculated by measuring the distance from the mean location of every spots to every restaurant. Then further duction was done based on the number of restaurants in the particular zone. The spots with less than or equal to 3 restaurants were selected. The spots are reduces to 14 at the end of the analysis. 

Most interesting fact is that nearly 9 out of 14 spots were located near the coast and another place to consider is the place near University of Toronto which mat attract the attention of college students.

## Conclusion

The purpose of the project is to find the best possible locations for the opening of new restaurant which may help the stackholders to decide the location of the restaurant. The best possible location was found from the analysis and plotted on the interactive ma 